Using SQL to update weather data

In [3]:
# sqlite3 library to run operations on the database
import sqlite3

gen_path = '/home/imants/gits/COVID-19/'

db_path = gen_path + 'sql/weather.db'

# connecting to the weather database
con = sqlite3.connect(db_path)

# establishing database cursor
cursorObj = con.cursor()


In [4]:
# Getting table names

import pandas as pd

table_names = cursorObj.execute("SELECT name FROM sqlite_master WHERE type='table';")

table_names = table_names.fetchall()

# Taking the table names that were fetched, and making a usable lists out of the values.

US_names = []
global_names = []

for x in range(len(table_names)):
    if (table_names[x][0][-2:] == 'US'):
        US_names.append(table_names[x][0])
        
    else:
        global_names.append(table_names[x][0])
        
 
print('US names', US_names)

print('Global names', global_names)
    


US names ['cloud_US', 'dew_US', 'humidity_US', 'ozone_US', 'precip_US', 'pressure_US', 'sunrise_US', 'sunset_US', 'tMax_US', 'tMin_US', 'uv_US', 'wind_US']
Global names ['cloud_Global', 'dew_Global', 'humidity_Global', 'ozone_Global', 'precip_Global', 'pressure_Global', 'sunrise_Global', 'sunset_Global', 'tMax_Global', 'tMin_Global', 'uv_Global', 'wind_Global']


In [ ]:
# getting table info

# query = 'SELECT * FROM {}'.format(US_names[0])
# cursorObj.execute(query)

# the_table = cursorObj.fetchall()

# the_table

In [21]:
# adding dates to tables
# current last date is 8/12/20

for x in range(14, 32):
    
    day_str = str(x)
    date_str = '"8/' + day_str + '/20"'
    
    for y in US_names:
        
        add_str = 'ALTER TABLE {} ADD COLUMN {} text'.format(y, date_str)
        cursorObj.execute(add_str)
        print(add_str)
    
    for y in global_names:
        
        add_str = 'ALTER TABLE {} ADD COLUMN {} text'.format(y, date_str)
        cursorObj.execute(add_str)
        print(add_str)

ALTER TABLE cloud_US ADD COLUMN "8/14/20" text
ALTER TABLE dew_US ADD COLUMN "8/14/20" text
ALTER TABLE humidity_US ADD COLUMN "8/14/20" text
ALTER TABLE ozone_US ADD COLUMN "8/14/20" text
ALTER TABLE precip_US ADD COLUMN "8/14/20" text
ALTER TABLE pressure_US ADD COLUMN "8/14/20" text
ALTER TABLE sunrise_US ADD COLUMN "8/14/20" text
ALTER TABLE sunset_US ADD COLUMN "8/14/20" text
ALTER TABLE tMax_US ADD COLUMN "8/14/20" text
ALTER TABLE tMin_US ADD COLUMN "8/14/20" text
ALTER TABLE uv_US ADD COLUMN "8/14/20" text
ALTER TABLE wind_US ADD COLUMN "8/14/20" text
ALTER TABLE cloud_US ADD COLUMN "8/15/20" text
ALTER TABLE dew_US ADD COLUMN "8/15/20" text
ALTER TABLE humidity_US ADD COLUMN "8/15/20" text
ALTER TABLE ozone_US ADD COLUMN "8/15/20" text
ALTER TABLE precip_US ADD COLUMN "8/15/20" text
ALTER TABLE pressure_US ADD COLUMN "8/15/20" text
ALTER TABLE sunrise_US ADD COLUMN "8/15/20" text
ALTER TABLE sunset_US ADD COLUMN "8/15/20" text
ALTER TABLE tMax_US ADD COLUMN "8/15/20" text
ALTE

ALTER TABLE cloud_US ADD COLUMN "8/29/20" text
ALTER TABLE dew_US ADD COLUMN "8/29/20" text
ALTER TABLE humidity_US ADD COLUMN "8/29/20" text
ALTER TABLE ozone_US ADD COLUMN "8/29/20" text
ALTER TABLE precip_US ADD COLUMN "8/29/20" text
ALTER TABLE pressure_US ADD COLUMN "8/29/20" text
ALTER TABLE sunrise_US ADD COLUMN "8/29/20" text
ALTER TABLE sunset_US ADD COLUMN "8/29/20" text
ALTER TABLE tMax_US ADD COLUMN "8/29/20" text
ALTER TABLE tMin_US ADD COLUMN "8/29/20" text
ALTER TABLE uv_US ADD COLUMN "8/29/20" text
ALTER TABLE wind_US ADD COLUMN "8/29/20" text
ALTER TABLE cloud_US ADD COLUMN "8/30/20" text
ALTER TABLE dew_US ADD COLUMN "8/30/20" text
ALTER TABLE humidity_US ADD COLUMN "8/30/20" text
ALTER TABLE ozone_US ADD COLUMN "8/30/20" text
ALTER TABLE precip_US ADD COLUMN "8/30/20" text
ALTER TABLE pressure_US ADD COLUMN "8/30/20" text
ALTER TABLE sunrise_US ADD COLUMN "8/30/20" text
ALTER TABLE sunset_US ADD COLUMN "8/30/20" text
ALTER TABLE tMax_US ADD COLUMN "8/30/20" text
ALTE

In [2]:
# Reading API key

key_path = '/home/imants/gits/COVID-19/key.txt'

api_file = open(key_path, 'r')
API_KEY = api_file.read()
api_file.close()
API_KEY = API_KEY.strip()

API_KEY

'4c660453101c9bb8a7f8360c95eaf4c1'

In [40]:
# update US locations

import pandas as pd
import numpy as np
import requests
import json
from datetime import datetime as dt

# Code to increase number of retries on connection errors,
# and also to give it some time.
# Found on https://stackoverflow.com/questions/15431044/can-i-set-max-retries-for-requests-request
# And https://findwork.dev/blog/advanced-usage-python-requests-timeouts-retries-hooks/

from urllib3.util.retry import Retry
from requests.adapters import HTTPAdapter

s = requests.Session()

retries = Retry(total=30,
                backoff_factor=0.1,
                status_forcelist=[ 429, 500, 502, 503, 504 ],
                method_whitelist=["HEAD", "GET", "OPTIONS"])

adapter = HTTPAdapter(max_retries=retries)
http = requests.Session()
http.mount("https://", adapter)
http.mount("http://", adapter)

# Dummy value in case of errors
dummy = -1000

# Making list of columns that need to be updated from prior update, above

columns_to_update = []

for x in range(13, 32):
    
    day_str = str(x)
    date_str = '"8/' + day_str + '/20"'
    columns_to_update.append(date_str)

for col_name in columns_to_update:
    
    tables = []
        
    for tab_name in US_names:
        
        query_string = 'SELECT Lat, "Long_", {} FROM {}'.format(col_name, tab_name)
        # print(query_string)
        cursorObj.execute(query_string)
        tables.append(cursorObj.fetchall())
        names_test = cursorObj.execute(query_string).description
        # print(names_test[2][0], col_name)
        
    # print(len(tables[0]))
   
    # Create Unix time stamp out of the date column
    # stripping quotation marks from column name
    i = len(col_name)
    col_date = col_name[1:(i-1)]
    
    t = pd.to_datetime(col_date)
    t = int(t.value / 10**9)
    t = str(t)
    
    for y in range(len(tables[0])):
        
        latitude = str(tables[0][y][0])
        longitude = str(tables[0][y][1])
        
        print('Latitude: ', latitude, ', Longitude: ', longitude, ', Date: ', col_name)
        print('Unix time: ', t)
        
        # Building the URL for the API get
        url = 'https://api.darksky.net/forecast/' + API_KEY + '/' + latitude + "," + longitude + ',' + t
        url = url + '?exclude=currently,flags&units=si'

        # Getting the API call
        # using the retry error handling established above
        response = http.get(url)
                
        # Putting the API response into the JSON thing
        info = json.loads(response.content)
    
        # adding error handling in case something is wrong with the JSON response
        try:

            # Making a variable to more easily acccess JSON response data
            easy_info = info['daily']['data'][0]

            # Reading the JSON data
            tMax = easy_info['temperatureHigh']
            tMin = easy_info['temperatureLow']
            hum = easy_info['humidity'] * 100
            uvee = easy_info['uvIndex']
            clouds = easy_info['cloudCover'] * 100
            precip = easy_info['precipProbability'] * 100
            dew = easy_info['dewPoint']
            pressure = easy_info['pressure']
            wind = easy_info['windSpeed']
            ozone = easy_info['ozone']
            sunrise = easy_info['sunriseTime']
            sunset = easy_info['sunsetTime']

        except:

            # Creating dummy values in case of error
            print('Error encountered')
            tMax = dummy
            tMin = dummy
            hum = dummy
            uvee = dummy
            clouds = dummy
            precip = dummy
            dew = dummy
            pressure = dummy
            wind = dummy
            ozone = dummy
            sunrise = dummy
            sunset = dummy
    
# test_string = 'SELECT Lat, "Long_", "8/13/20" FROM cloud_US'

# cursorObj.execute(test_string)

# the_table = cursorObj.fetchall()

#the_table[0]
#print(tables[0][0])
#names_test = tables[0].description

#print(names_test)

Latitude:  32.53952745 , Longitude:  -86.64408227 , Date:  "8/13/20"
Unix time:  1597276800
Latitude:  30.72774991 , Longitude:  -87.72207058 , Date:  "8/13/20"
Unix time:  1597276800
Latitude:  31.868263 , Longitude:  -85.3871286 , Date:  "8/13/20"
Unix time:  1597276800
Latitude:  32.99642064 , Longitude:  -87.12511459999996 , Date:  "8/13/20"
Unix time:  1597276800
Latitude:  33.98210918 , Longitude:  -86.56790593 , Date:  "8/13/20"
Unix time:  1597276800
Latitude:  32.10030533 , Longitude:  -85.71265535 , Date:  "8/13/20"
Unix time:  1597276800
Latitude:  31.75300095 , Longitude:  -86.68057478 , Date:  "8/13/20"
Unix time:  1597276800
Latitude:  33.77483727 , Longitude:  -85.82630386 , Date:  "8/13/20"
Unix time:  1597276800
Latitude:  32.91360079 , Longitude:  -85.39072749 , Date:  "8/13/20"
Unix time:  1597276800
Latitude:  34.17805983 , Longitude:  -85.60638968 , Date:  "8/13/20"
Unix time:  1597276800
Latitude:  32.85044126 , Longitude:  -86.7173256 , Date:  "8/13/20"
Unix time

Latitude:  36.33644656 , Longitude:  -94.25680817 , Date:  "8/13/20"
Unix time:  1597276800
Latitude:  36.3084504 , Longitude:  -93.09374925 , Date:  "8/13/20"
Unix time:  1597276800
Latitude:  33.46755808 , Longitude:  -92.15980837 , Date:  "8/13/20"
Unix time:  1597276800
Latitude:  33.55598792 , Longitude:  -92.49974403 , Date:  "8/13/20"
Unix time:  1597276800
Latitude:  36.34038560000001 , Longitude:  -93.54270261 , Date:  "8/13/20"
Unix time:  1597276800
Latitude:  33.26458973 , Longitude:  -91.29539209 , Date:  "8/13/20"
Unix time:  1597276800
Latitude:  34.04613432 , Longitude:  -93.17484713 , Date:  "8/13/20"
Unix time:  1597276800
Latitude:  36.36826212 , Longitude:  -90.4148172 , Date:  "8/13/20"
Unix time:  1597276800
Latitude:  35.53864922 , Longitude:  -92.02640019 , Date:  "8/13/20"
Unix time:  1597276800
Latitude:  33.89723187 , Longitude:  -92.18537045 , Date:  "8/13/20"
Unix time:  1597276800
Latitude:  33.21230701 , Longitude:  -93.22642793 , Date:  "8/13/20"
Unix ti

Latitude:  34.65329488 , Longitude:  -120.0188492 , Date:  "8/13/20"
Unix time:  1597276800
Latitude:  37.23104908 , Longitude:  -121.6970462 , Date:  "8/13/20"
Unix time:  1597276800
Latitude:  37.05580291 , Longitude:  -122.0066524 , Date:  "8/13/20"
Unix time:  1597276800
Latitude:  40.76391419 , Longitude:  -122.0396884 , Date:  "8/13/20"
Unix time:  1597276800
Latitude:  39.57713498 , Longitude:  -120.52007009999998 , Date:  "8/13/20"
Unix time:  1597276800
Latitude:  41.59198861 , Longitude:  -122.5407434 , Date:  "8/13/20"
Unix time:  1597276800
Latitude:  38.26827353 , Longitude:  -121.9357113 , Date:  "8/13/20"
Unix time:  1597276800
Latitude:  38.52746429 , Longitude:  -122.8862506 , Date:  "8/13/20"
Unix time:  1597276800
Latitude:  37.55862499 , Longitude:  -120.9970722 , Date:  "8/13/20"
Unix time:  1597276800
Latitude:  39.03417539 , Longitude:  -121.6945899 , Date:  "8/13/20"
Unix time:  1597276800
Latitude:  40.12570935 , Longitude:  -122.2370171 , Date:  "8/13/20"
Unix

Unix time:  1597276800
Latitude:  29.83791238 , Longitude:  -84.82731662 , Date:  "8/13/20"
Unix time:  1597276800
Latitude:  30.57796289 , Longitude:  -84.61915825 , Date:  "8/13/20"
Unix time:  1597276800
Latitude:  29.72856978 , Longitude:  -82.79880657 , Date:  "8/13/20"
Unix time:  1597276800
Latitude:  26.95635849 , Longitude:  -81.18996211 , Date:  "8/13/20"
Unix time:  1597276800
Latitude:  29.93543004 , Longitude:  -85.24270990000002 , Date:  "8/13/20"
Unix time:  1597276800
Latitude:  30.49673973 , Longitude:  -82.94998918 , Date:  "8/13/20"
Unix time:  1597276800
Latitude:  27.49293939 , Longitude:  -81.80956574 , Date:  "8/13/20"
Unix time:  1597276800
Latitude:  26.55386945 , Longitude:  -81.16469006 , Date:  "8/13/20"
Unix time:  1597276800
Latitude:  28.55364461 , Longitude:  -82.42700204 , Date:  "8/13/20"
Unix time:  1597276800
Latitude:  27.34254618 , Longitude:  -81.34071957 , Date:  "8/13/20"
Unix time:  1597276800
Latitude:  27.9276559 , Longitude:  -82.32013172 , 

Latitude:  31.53328528 , Longitude:  -84.21722377 , Date:  "8/13/20"
Unix time:  1597276800
Latitude:  33.70291126 , Longitude:  -84.77026156 , Date:  "8/13/20"
Unix time:  1597276800
Latitude:  31.32155345 , Longitude:  -84.90255207 , Date:  "8/13/20"
Unix time:  1597276800
Latitude:  30.71101099 , Longitude:  -82.89687287 , Date:  "8/13/20"
Unix time:  1597276800
Latitude:  32.36616021 , Longitude:  -81.34280942 , Date:  "8/13/20"
Unix time:  1597276800
Latitude:  34.11302332 , Longitude:  -82.83936148 , Date:  "8/13/20"
Unix time:  1597276800
Latitude:  32.59221302 , Longitude:  -82.30239915 , Date:  "8/13/20"
Unix time:  1597276800
Latitude:  32.15328841 , Longitude:  -81.8870105 , Date:  "8/13/20"
Unix time:  1597276800
Latitude:  34.86430205 , Longitude:  -84.316964 , Date:  "8/13/20"
Unix time:  1597276800
Latitude:  33.41357794 , Longitude:  -84.49089434 , Date:  "8/13/20"
Unix time:  1597276800
Latitude:  34.26268279 , Longitude:  -85.21577392 , Date:  "8/13/20"
Unix time:  15

...

Unix time:  1598832000
Latitude:  31.43052248 , Longitude:  -102.5143314 , Date:  "8/31/20"
Unix time:  1598832000
Latitude:  30.72367027 , Longitude:  -101.4134238 , Date:  "8/31/20"
Unix time:  1598832000
Latitude:  33.61431553 , Longitude:  -101.3000364 , Date:  "8/31/20"
Unix time:  1598832000
Latitude:  31.44506775 , Longitude:  -104.5185739 , Date:  "8/31/20"
Unix time:  1598832000
Latitude:  36.27787176 , Longitude:  -102.6020725 , Date:  "8/31/20"
Unix time:  1598832000
Latitude:  32.76670599 , Longitude:  -96.7779605 , Date:  "8/31/20"
Unix time:  1598832000
Latitude:  32.74255572 , Longitude:  -101.9477242 , Date:  "8/31/20"
Unix time:  1598832000
Latitude:  29.08101855 , Longitude:  -97.3568117 , Date:  "8/31/20"
Unix time:  1598832000
Latitude:  34.96522957 , Longitude:  -102.6054267 , Date:  "8/31/20"
Unix time:  1598832000
Latitude:  33.38570922 , Longitude:  -95.66921122 , Date:  "8/31/20"
Unix time:  1598832000
Latitude:  33.20521901 , Longitude:  -97.11691153 , Date:  

Latitude:  33.67521893 , Longitude:  -97.72500958 , Date:  "8/31/20"
Unix time:  1598832000
Latitude:  30.30079133 , Longitude:  -95.50572772 , Date:  "8/31/20"
Unix time:  1598832000
Latitude:  35.83769242 , Longitude:  -101.8930281 , Date:  "8/31/20"
Unix time:  1598832000
Latitude:  33.11304005 , Longitude:  -94.73255695 , Date:  "8/31/20"
Unix time:  1598832000
Latitude:  34.07408766 , Longitude:  -100.779722 , Date:  "8/31/20"
Unix time:  1598832000
Latitude:  31.62017125 , Longitude:  -94.61803994 , Date:  "8/31/20"
Unix time:  1598832000
Latitude:  32.04620681 , Longitude:  -96.47428766 , Date:  "8/31/20"
Unix time:  1598832000
Latitude:  30.78548982 , Longitude:  -93.74408813 , Date:  "8/31/20"
Unix time:  1598832000
Latitude:  32.30365282 , Longitude:  -100.4060208 , Date:  "8/31/20"
Unix time:  1598832000
Latitude:  27.736286 , Longitude:  -97.5433285 , Date:  "8/31/20"
Unix time:  1598832000
Latitude:  36.27829105 , Longitude:  -100.8158184 , Date:  "8/31/20"
Unix time:  159

Latitude:  39.70208397 , Longitude:  -112.7809245 , Date:  "8/31/20"
Unix time:  1598832000
Latitude:  37.28507306 , Longitude:  -111.8861752 , Date:  "8/31/20"
Unix time:  1598832000
Latitude:  39.0729209 , Longitude:  -113.1020328 , Date:  "8/31/20"
Unix time:  1598832000
Latitude:  41.08830262 , Longitude:  -111.5727723 , Date:  "8/31/20"
Unix time:  1598832000
Latitude:  38.33815254 , Longitude:  -112.1249591 , Date:  "8/31/20"
Unix time:  1598832000
Latitude:  41.63137678 , Longitude:  -111.2445105 , Date:  "8/31/20"
Unix time:  1598832000
Latitude:  40.66616532 , Longitude:  -111.9216011 , Date:  "8/31/20"
Unix time:  1598832000
Latitude:  37.62762978 , Longitude:  -109.80337140000002 , Date:  "8/31/20"
Unix time:  1598832000
Latitude:  39.37231946 , Longitude:  -111.5758676 , Date:  "8/31/20"
Unix time:  1598832000
Latitude:  38.74837146 , Longitude:  -111.8050275 , Date:  "8/31/20"
Unix time:  1598832000
Latitude:  38.99617072 , Longitude:  -110.7013958 , Date:  "8/31/20"
Unix 

Latitude:  38.7464321 , Longitude:  -77.48509905 , Date:  "8/31/20"
Unix time:  1598832000
Latitude:  38.77058531 , Longitude:  -77.44399307 , Date:  "8/31/20"
Unix time:  1598832000
Latitude:  36.68212094 , Longitude:  -79.86352771 , Date:  "8/31/20"
Unix time:  1598832000
Latitude:  37.44164146 , Longitude:  -76.34098896 , Date:  "8/31/20"
Unix time:  1598832000
Latitude:  36.67882005 , Longitude:  -78.36131056 , Date:  "8/31/20"
Unix time:  1598832000
Latitude:  37.63191998 , Longitude:  -76.55064617 , Date:  "8/31/20"
Unix time:  1598832000
Latitude:  37.17746986 , Longitude:  -80.37868691 , Date:  "8/31/20"
Unix time:  1598832000
Latitude:  37.78790447 , Longitude:  -78.88498513 , Date:  "8/31/20"
Unix time:  1598832000
Latitude:  37.50694406 , Longitude:  -76.99828634 , Date:  "8/31/20"
Unix time:  1598832000
Latitude:  37.08166899 , Longitude:  -76.51754109 , Date:  "8/31/20"
Unix time:  1598832000
Latitude:  36.89934014 , Longitude:  -76.26420872 , Date:  "8/31/20"
Unix time:  

Latitude:  44.95856458 , Longitude:  -87.30002707 , Date:  "8/31/20"
Unix time:  1598832000
Latitude:  46.43222285 , Longitude:  -91.91595768 , Date:  "8/31/20"
Unix time:  1598832000
Latitude:  44.94562799 , Longitude:  -91.8962481 , Date:  "8/31/20"
Unix time:  1598832000
Latitude:  44.726614 , Longitude:  -91.28609183 , Date:  "8/31/20"
Unix time:  1598832000
Latitude:  45.84963535 , Longitude:  -88.39804137 , Date:  "8/31/20"
Unix time:  1598832000
Latitude:  43.75354908 , Longitude:  -88.48885325 , Date:  "8/31/20"
Unix time:  1598832000
Latitude:  45.66678019 , Longitude:  -88.77084892 , Date:  "8/31/20"
Unix time:  1598832000
Latitude:  42.8671731 , Longitude:  -90.7063218 , Date:  "8/31/20"
Unix time:  1598832000
Latitude:  42.6794956 , Longitude:  -89.60243287 , Date:  "8/31/20"
Unix time:  1598832000
Latitude:  43.80025981 , Longitude:  -89.04679553 , Date:  "8/31/20"
Unix time:  1598832000
Latitude:  43.00050278 , Longitude:  -90.13469017 , Date:  "8/31/20"
Unix time:  15988

In [16]:
for x in range(len(the_table)):
    print(x)

0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
275
276
27

2168
2169
2170
2171
2172
2173
2174
2175
2176
2177
2178
2179
2180
2181
2182
2183
2184
2185
2186
2187
2188
2189
2190
2191
2192
2193
2194
2195
2196
2197
2198
2199
2200
2201
2202
2203
2204
2205
2206
2207
2208
2209
2210
2211
2212
2213
2214
2215
2216
2217
2218
2219
2220
2221
2222
2223
2224
2225
2226
2227
2228
2229
2230
2231
2232
2233
2234
2235
2236
2237
2238
2239
2240
2241
2242
2243
2244
2245
2246
2247
2248
2249
2250
2251
2252
2253
2254
2255
2256
2257
2258
2259
2260
2261
2262
2263
2264
2265
2266
2267
2268
2269
2270
2271
2272
2273
2274
2275
2276
2277
2278
2279
2280
2281
2282
2283
2284
2285
2286
2287
2288
2289
2290
2291
2292
2293
2294
2295
2296
2297
2298
2299
2300
2301
2302
2303
2304
2305
2306
2307
2308
2309
2310
2311
2312
2313
2314
2315
2316
2317
2318
2319
2320
2321
2322
2323
2324
2325
2326
2327
2328
2329
2330
2331
2332
2333
2334
2335
2336
2337
2338
2339
2340
2341
2342
2343
2344
2345
2346
2347
2348
2349
2350
2351
2352
2353
2354
2355
2356
2357
2358
2359
2360
2361
2362
2363
2364
2365
2366
2367


In [22]:
# close database connection

con.close()